In [22]:
import numpy as np
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
from magenta.models.score2perf import score2perf
from tensor2tensor.data_generators import text_encoder
import note_seq

## Helper Functions

In [23]:
def decode(ids, encoder):
    ids = list(ids)
    if text_encoder.EOS_ID in ids:
        ids = ids[:ids.index(text_encoder.EOS_ID)]
    return encoder.decode(ids)

In [24]:
def load_midi(midi_file_path):
    return note_seq.midi_file_to_note_sequence(midi_file_path)

## Unconditioned Model

In [25]:
class PianoPerformanceLanguageModelProblem(score2perf.Score2PerfProblem):
  @property
  def add_eos_symbol(self):
    return True

In [26]:
problem = PianoPerformanceLanguageModelProblem()

In [27]:
from tensor2tensor import problems
unconditional_encoders = problem.get_feature_encoders()

In [28]:
from tensor2tensor.utils import trainer_lib
hparams = trainer_lib.create_hparams(hparams_set='transformer_tpu')
trainer_lib.add_problem_hparams(hparams, problem)
hparams.num_hidden_layers = 16
hparams.sampling_method = 'random'

In [29]:
from tensor2tensor.utils import decoding
decode_hparams = decoding.decode_hparams()
decode_hparams.alpha = 0.0
decode_hparams.beam_size = 1

In [30]:
run_config = trainer_lib.create_run_config(hparams)
estimator = trainer_lib.create_estimator(
    'transformer', hparams, run_config,
    decode_hparams=decode_hparams)

INFO:tensorflow:Configuring DataParallelism to replicate the model.


INFO:tensorflow:Configuring DataParallelism to replicate the model.


INFO:tensorflow:schedule=continuous_train_and_eval


INFO:tensorflow:schedule=continuous_train_and_eval


INFO:tensorflow:worker_gpu=1


...

INFO:tensorflow:caching_devices: None


INFO:tensorflow:ps_devices: ['gpu:0']


INFO:tensorflow:ps_devices: ['gpu:0']


INFO:tensorflow:Using config: {'_model_dir': '/var/folders/m3/6svr5sf15rv9b8y0fpsbygfw0000gp/T/tmpnl9aswv_', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 1000, '_save_checkpoints_secs': None, '_session_config': gpu_options {
  per_process_gpu_memory_fraction: 0.95
}
allow_soft_placement: true
graph_options {
  optimizer_options {
    global_jit_level: OFF
  }
}
isolate_session_state: true
, '_keep_checkpoint_max': 20, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas':

INFO:tensorflow:Using config: {'_model_dir': '/var/folders/m3/6svr5sf15rv9b8y0fpsbygfw0000gp/T/tmpnl9aswv_', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': 1000, '_save_checkpoints_secs': None, '_session_config': gpu_options {
  per_process_gpu_memory_fraction: 0.95
}
allow_soft_placement: true
graph_options {
  optimizer_options {
    global_jit_level: OFF
  }
}
isolate_session_state: true
, '_keep_checkpoint_max': 20, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas':

In [31]:
ckpt_path = 'models/music_transformer/unconditional_model_16.ckpt'

In [32]:
def input_generator():
    global targets
    global decode_length
    while True:
        print('yielding', len(targets))
        yield {
            'targets': np.array([targets], dtype=np.int32),
            'decode_length': np.array(decode_length, dtype=np.int32)
        }

In [33]:
targets = []
decode_length = 0

In [34]:
input_fn = decoding.make_input_fn_from_generator(input_generator())
unconditional_samples = estimator.predict(
    input_fn, checkpoint_path=ckpt_path)

yielding 0


In [ ]:
_ = next(unconditional_samples)

In [36]:
targets = []
decode_length = 1024
sample_ids = next(unconditional_samples)['outputs']

yielding 0


In [37]:
midi_filename = decode(
    sample_ids,
    encoder=unconditional_encoders['targets'])

In [38]:
unconditional_ns = note_seq.midi_file_to_note_sequence(midi_filename)

In [39]:
note_seq.plot_sequence(unconditional_ns)

Loading BokehJS ...

In [47]:
SF2_PATH = 'soundfonts/Yamaha-C5-Salamander-JNv5.1.sf2'
SAMPLE_RATE = float(44100)

In [48]:
note_seq.play_sequence(unconditional_ns, synth=note_seq.fluidsynth, sample_rate=SAMPLE_RATE, sf2_path=SF2_PATH)

In [42]:
import shutil
shutil.copyfile(midi_filename, 'output.midi')

'output.midi'